# Waveform fitting

In [1]:
# Setup ipython environment
%load_ext autoreload
%autoreload 2
%matplotlib inline
# Setup the notebook's environment
import lalsimulation as lalsim
from matplotlib.pyplot import *
from numpy import *
from positive import *
from nrutils import scsearch, gwylm
from glob import glob
import xcp
from xcp import determine_data_fitting_region,calibration_catalog,metadata_dict,template_amp_phase

(positive)>> Applying custom matplotlib settings.
(init)>> Warm greetings from XCP.
(xcp.core)>> Catalog of calibration runs stored to "xcp.calibration_catalog"
(xcp.core)>> Metadata dictionary for calibration runs stored to "xcp.metadata_dict"
(xcp.core)>> Metadata dictionary for Ed's catalog paper stored to "xcp.catalog_paper_metadata"


In [2]:
# Let the user know where lalsimulation lives

#
lalsim_path = lalsim.__path__[0]
lalsuite_repo_path = lalsim_path.split('lib')[0]+'src/lalsuite/'
branch_name = bash('cd %s && git status'%lalsuite_repo_path).decode("utf-8").split('On branch ')[-1].split('\n')[0]

#
alert('We are getting our LALSimulation from:\n%s'%magenta(lalsim_path))
alert('We think that the related lalsuite source files are here:\n%s'%green(lalsuite_repo_path))
alert('Lastly, we are currently on this branch: %s'%bold(magenta(branch_name)))

#
if branch_name != 'pnrv1-ll':
    alert('We are not on the expected branch. This may cause unexpected behavior.',say=True)

(notebook)>> We are getting our LALSimulation from:
/Users/book/opt/anaconda2/envs/hack-phenomx3/lib/python3.6/site-packages/lalsimulation
(notebook)>> We think that the related lalsuite source files are here:
/Users/book/opt/anaconda2/envs/hack-phenomx3/src/lalsuite/
(notebook)>> Lastly, we are currently on this branch: pnrv1-ll


## This notebook is for prototyping and scratch code only. Please see scripts with same issue number.

In [21]:
zeros(3)

array([0., 0., 0.])

In [28]:
parameter_names = action_helper.__code__.co_varnames[1:action_helper.__code__.co_argcount]

In [20]:
action_helper.__code__.co_argcount

9

In [9]:

#
from numpy.linalg import norm
from scipy.optimize import curve_fit,minimize,fmin

#
ll = 2

#
datadir = '/Users/book/KOALA/PhenomXCP/data/version2/'
files = glob( datadir+'*_l%im%i.txt'%(ll,ll) )
files.sort()

files = files[::-1]

#
fig,ax = subplots( len(files), 2, figsize=3*array([ 2.5*2/(0.618), 2.0*len(files) ]) )
# fig,ax = subplots( 1, 2, figsize=3*array([ 2.5*2/(0.618), 2.5*1 ]), sharex=True)
ax = ax.flatten()

#
tight_layout(1,2,4)

#
foo = {}

#
lmlist = [ (ll,ll) ]

#
p = 0
for f_ in files[::-1]:
    
    if True:#'q8a08t90' in f_:#'q8a08t30' in f_:

        #
        simname = f_.split('/')[-1].split('_l%im%i.'%(ll,ll))[0]

        # Find index location of metadata for simname 
        k = [ k for k,val in enumerate(metadata_dict['simname']) if val in simname ][0]

        # Load data for this case
        raw_data = loadtxt(f_).T
        calibration_data, dphi_lorentzian_min, f_min, f_max, f_lorentzian_min = determine_data_fitting_region( raw_data )

        # Collect params for this case 
        metadata = metadata_dict['array_data'][k,:]

        #
        f,amp_fd,dphi_fd,alpha,beta,gamma = calibration_data.T
        theta,m1,m2,eta,delta,chi_eff,chi_p,chi1,chi2,a1,a2,chi1_vec,chi2_vec = metadata_dict['array_data'][k]
        #dphi_fd -= min( dphi_fd[ (f>0.03)&(f<0.12) ] )
        
        #
        action_helper = template_amp_phase(m1, m2, chi1_vec, chi2_vec,ell=2)
        def action( p ):
            #
            amplitude,phase_derivative = action_helper( f, *p )
            # -- Calculate residual of phase derivative -- #
            residual_phase_derivative = sum((dphi_fd - phase_derivative)**2) / std(dphi_fd)
            # -- Calculate residual of amplitude --------- #
            amp_scale = f ** (7.0/6)
            inv_amp_scale = f ** (-7.0/6)
            log_scaled_amp_fd = log( amp_fd * amp_scale )
            log_scaled_amplitude = log( amplitude * amp_scale )
            residual_amplitude = sum((log_scaled_amp_fd - log_scaled_amplitude)**2) / std(log_scaled_amp_fd)
            # -- Combine residuals ----------------------- #
            combined_residual = residual_phase_derivative + residual_amplitude
            #
            return combined_residual
        
        #
        foo = minimize( action,[0,0,0,0,0,0,0,0] )
        best_fit_amp,best_fit_dphi = action_helper( f, *foo.x )
#         print(foo.x)
        
        #
        mod_xhm0_amp,mod_xhm0_dphi = action_helper(f)
        
        
        
#         # GENERATE TEMPLATE FUNCTIONS
#         # ---
#         template_amp, make_template_dphi = template_amp_phase(m1, m2, chi1_vec, chi2_vec,ell=2)
#         mod_xhm0_amp  = template_amp(f)
#         mod_xhm0_dphi = make_template_dphi()(f)
        
#         #
#         mod_xhm_dict = xcp.get_phenomxphm_coprecessing_multipoles( f,lmlist, m1, m2, chi1_vec, chi2_vec )
#         mod_xhm = mod_xhm_dict[ll,ll]
#         mod_xhm_amp = abs(mod_xhm)
#         mod_xhm_phi = unwrap( angle(mod_xhm) )
#         mod_xhm_dphi = spline_diff(f,mod_xhm_phi)
#         mod_xhm_dphi -= min( mod_xhm_dphi[ (f>0.03)&(f<0.12) ] )   

#         # AMPLITUDE
#         # ---

#         #
#         amp_scale = f ** (7.0/6)
#         inv_amp_scale = f ** (-7.0/6)

#         #
#         log_scaled_template_amp = lambda X,MU2,NU5,NU6: log(  template_amp(X,MU2,NU5)*amp_scale  )
#         phenomd_amp = template_amp(f)

#         #
#         scaled_amp_fd = amp_fd * amp_scale
#         log_scaled_amp_fd = log(scaled_amp_fd)
#         log_scaled_amp_popt, log_amp_pcov = curve_fit(log_scaled_template_amp, f, log_scaled_amp_fd,p0=[0,0])
#         best_fit_amp = exp(log_scaled_template_amp(f,*log_scaled_amp_popt)) * inv_amp_scale
#         print(log_scaled_amp_popt)
        
#         # MAKE PHASE DERIVATIVE TEMPLATE USING AMP FIT
#         # --- 
#         opt_mu2, opt_nu5, opt_nu6 = log_scaled_amp_popt
#         template_dphi = make_template_dphi( nu5=opt_nu5, nu6=opt_nu6 )

#         # PHASE DERIVATIVE
#         # ---

#         # #
#         # alert('trying to tune ...')
#         # reduced_dphi_template = template_dphi( f,  )
#         # dphi_popt, dphi_pcov = curve_fit(template_dphi, f, dphi_fd,p0=[0,0])
#         # print(dphi_popt)
#         # best_fit_dphi = template_dphi(f,*dphi_popt)
#         best_fit_dphi = template_dphi(f)

        # PLOTTING
        # ---

        #
        sca(ax[p]); p+=1
#         #plot( f, phenomd_dphi, label='PhenomD', ls='--',alpha=0.3,color='k' )
        plot( f, dphi_fd, label='Calibration Data (NR)', lw=4,ls='-', alpha=0.15, color='k' )
#         plot( f, mod_xhm_dphi, label='PhenomX(500)', ls='--',lw=1,alpha=0.85,color='b' )
        plot( f, mod_xhm0_dphi, label='PhenomX(0)', ls='--',lw=1,alpha=0.85,color='k',zorder=-10 )
        plot( f, best_fit_dphi, label='Best Fit', color='r', ls='-' )
        xscale('log')
        xlim(lim(f,dilate=1.1,dilate_with_multiply=True))
        ylim( limy(f, dphi_fd,dilate=0.1) )
#         #plot( f, best_fit_dphi2, label='Best Fit (phi fit)', color='b', ls='-' )
        title(simname,size=12,loc='left')
        legend(ncol=2,loc=1)
        ylabel(r'$\frac{d}{df}\arg(\tilde{h}_{22})$')
        xlabel('$fM$')
#         if p==(len(files)-2):  xlabel('$fM$')
#         #
        title(simname,loc='left',size=12)

#         #subplot(1,2,2)
        sca(ax[p]); p+=1
#         plot( f, phenomd_amp, label='PhenomD', ls='--',alpha=0.9,color='k' )
        plot( f, amp_fd, label='Calibration Data (NR)', lw=4,ls='-', alpha=0.15, color='k' )
#         plot( f, mod_xhm_amp, label='PhenomX(500)', ls='--',lw=1,alpha=0.85,color='b' )
        plot( f, mod_xhm0_amp, label='PhenomX(0)', ls='--',lw=1,alpha=0.85,color='k',zorder=-10 )
        plot( f, best_fit_amp, label='Best Fit', color='r', ls='-' )
#         title(simname,size=12,loc='left')
        yscale('log')
        xscale('log')
        legend(ncol=2,loc=3)
        ylim( limy(f, amp_fd,dilate=1.2) )
        xlabel('$fM$')
        ylabel(r'$|\tilde{h}_{22}(f)|$')
        #
        title(simname,loc='left',size=12)
        
#         #
#         figure()
#         mask = (f>0.03) & (f<0.12)
#         plot( f, phenomd_phi, label='PhenomD', ls='--',alpha=0.9,color='k' )
#         plot( f, phi_td, label='NR:Precessing', color='k', alpha=0.15, lw=6 )
#         plot( f, best_fit_phi, label='Best Fit', color='r', ls='-' )
#         plot( f, best_fit_phi_from_dphi_fit, label='Best Fit 2', color='b', ls='-' )

#         figure()
#         plot( f,best_fit_phi-phi_td, label='from phase fit' )
#         plot( f,best_fit_phi_from_dphi_fit-phi_td, label='from dphase fit' )
#         legend()
        
        #
#         break
        
#
file_path = datadir+'waveform_fit_diagnostic_l%im%i.pdf'%(ll,ll)
alert('Saving batch plot to %s'%magenta(file_path))
savefig(file_path,pad_inches=2, bbox_inches = "tight")
alert('Done.')

/Users/book/opt/anaconda2/envs/hack-phenomx3/lib/python3.6/site-packages/ipykernel_launcher.py:21: MatplotlibDeprecationWarning: Passing the pad parameter of tight_layout() positionally is deprecated since Matplotlib 3.3; the parameter will become keyword-only two minor releases later.


(notebook)>> Saving batch plot to /Users/book/KOALA/PhenomXCP/data/version2/waveform_fit_diagnostic_l2m2.pdf
(notebook)>> Done.


In [4]:
?minimize

Signature:
minimize(
    fun,
    x0,
    args=(),
    method=None,
    jac=None,
    hess=None,
    hessp=None,
    bounds=None,
    constraints=(),
    tol=None,
    callback=None,
    options=None,
)
Docstring:
Minimization of scalar function of one or more variables.

Parameters
----------
fun : callable
    The objective function to be minimized.

        ``fun(x, *args) -> float``

    where ``x`` is an 1-D array with shape (n,) and ``args``
    is a tuple of the fixed parameters needed to completely
    specify the function.
x0 : ndarray, shape (n,)
    Initial guess. Array of real elements of size (n,),
    where 'n' is the number of independent variables.
args : tuple, optional
    Extra arguments passed to the objective function and its
    derivatives (`fun`, `jac` and `hess` functions).
method : str or callable, optional
    Type of solver.  Should be one of

        - 'Nelder-Mead' :ref:`(see here) <optimize.minimize-neldermead>`
        - 'Powell'      :ref:`(see here) <o

In [10]:
foo

(xcp.core)>> Catalog of calibration runs stored to "xcp.calibration_catalog"
(xcp.core)>> Metadata dictionary for calibration runs stored to "xcp.metadata_dict"
(xcp.core)>> Metadata dictionary for Ed's catalog paper stored to "xcp.catalog_paper_metadata"


      fun: 209.89165770738484
 hess_inv: array([[ 1.70242093e-03,  3.10398174e-03,  2.08911686e-03,
         9.21367317e-09, -1.63482177e-06,  2.66365058e-06,
        -5.08058625e-06,  3.61351199e-04],
       [ 3.10398174e-03,  2.00257171e-02,  3.25656104e-02,
         1.06243684e-06,  4.58632880e-05, -4.12350510e-05,
         4.80547359e-05, -3.45060119e-03],
       [ 2.08911686e-03,  3.25656104e-02,  7.46343836e-02,
         2.62833884e-06,  1.31546943e-04, -1.41288420e-04,
         1.63653446e-04, -1.18189717e-02],
       [ 9.21367281e-09,  1.06243684e-06,  2.62833884e-06,
         2.31206906e-10,  9.02678417e-09, -9.59637122e-09,
         5.36323709e-09, -3.34429497e-07],
       [-1.63482177e-06,  4.58632880e-05,  1.31546943e-04,
         9.02678416e-09,  5.60335539e-07, -5.64318191e-07,
         5.96045070e-07, -4.25663410e-05],
       [ 2.66365059e-06, -4.12350510e-05, -1.41288420e-04,
        -9.59637122e-09, -5.64318191e-07,  6.54225586e-07,
        -5.80219024e-07,  4.12192452

In [6]:
# [print( k) for k in lal.__dict__.keys() if 'real8' in k.lower()];
# ?lal.CreateREAL8Value
test = lal.CreateREAL8Value(3)
print( test.__dict__.keys() )

dict_keys([])
